In [1]:
import pandas as pd
import networkx as nx
from sklearn.metrics import roc_auc_score

In [2]:
day1 = pd.read_parquet("part-00156-0d84e01b-458f-4875-854c-cab58ad5aaf5.c000.snappy.parquet")

In [3]:
tr = day1.groupby(["src_identity","dst_identity"]).sum().reset_index()

In [4]:
def net_from_tr(df,threashold_value=100000000,threshold_repetitions=5):
    tr = df.groupby(["src_identity","dst_identity"]).sum().reset_index()
    repet_dst = tr['dst_identity'].value_counts()
    repet_src = tr['src_identity'].value_counts()
    tr = tr[tr['dst_identity'].isin(repet_dst[repet_dst>=threshold_repetitions].index)]
    tr = tr[tr['src_identity'].isin(repet_src[repet_src>=threshold_repetitions].index)]


    tr_noloop=tr[tr["src_identity"]!=tr["dst_identity"]].sort_values("value")
    tr_large = tr_noloop[tr_noloop["value"]>threashold_value]
    large_g = nx.from_pandas_edgelist(tr_large,source="src_identity",target="dst_identity",edge_attr="value")
    return tr_large,large_g

In [5]:
day1 = pd.read_parquet("part-00156-0d84e01b-458f-4875-854c-cab58ad5aaf5.c000.snappy.parquet")

In [6]:
df1,g1 = net_from_tr(day1)

In [7]:
len(g1.nodes)

459

In [8]:
nx.write_graphml(g1,"test2.graphml")

In [9]:
predictions_on = list(g1.nodes)

In [10]:
day2 = pd.read_parquet("part-00163-0d84e01b-458f-4875-854c-cab58ad5aaf5.c000.snappy.parquet")

In [11]:
df2,g2 = net_from_tr(day2)

In [12]:
PA = nx.preferential_attachment(g1)
AA = nx.adamic_adar_index(g1)
prediction = pd.DataFrame.from_records(list(AA),columns=["n1","n2","score"])
#pouet = pd.DataFrame.from_records(list(PA),columns=["n1","n2","score"])

In [13]:
scores=[]
classe=[]
pairs=[]
for i,row in prediction.iterrows():
    u = row["n1"]
    v=row["n2"]
    if u in g2 and v in g2 and not g1.has_edge(u,v):
        if g2.has_edge(u,v):
            classe.append(1)
        else:
            classe.append(0)
        scores.append(row["score"])
        pairs.append((u,v))

In [14]:
roc_auc_score(classe,scores)

0.7506603285424116

In [15]:
test =pd.DataFrame()

In [16]:
test["scores"]=scores
test["classe"]=classe
test["pairs"]=pairs

In [17]:
test.sort_values("scores",ascending=False)[:50]

scores  classe                                  pairs
7501   4.540307       0                  (0, Bitstamp.net-old)
11326  4.422833       1        (AgoraMarket, Bitstamp.net-old)
9001   4.418558       1          (ePay.info, Bitstamp.net-old)
3034   4.259891       1       (Cryptsy.com, Bitfinex.com-old2)
2922   4.171256       0             (Cryptsy.com, AgoraMarket)
3912   3.840217       0                      (2226, ePay.info)
10160  3.776366       0       (Bitfinex.com-old2, AgoraMarket)
8945   3.709215       0              (ePay.info, Poloniex.com)
10162  3.566595       1      (Bitfinex.com-old2, OKCoin.com-2)
5464   3.564195       1             (Bittrex.com, Huobi.com-2)
36     3.497987       1                  (Cex.io, Cryptsy.com)
5487   3.367685       0        (Bittrex.com, BTC-e.com-output)
14444  3.220618       0                    (OKCoin.com-2, 424)
7528   3.175215       0                    (0, CoinTrader.net)
7491   3.175215       0                        (0, AnxPro.com)
759    3.175215       0             (LocalBitcoins.com-old, 0)
7556   3.145420       1                         (0, BTC-e.com)
3028   3.128576       0         (Cryptsy.com, EvolutionMarket)
3015   3.121136       0                     (Cryptsy.com, 424)
9007   3.041453       0              (ePay.info, Hashnest.com)
7883   2.827662       1                (Kraken.com, ePay.info)
14779  2.820214       0                       (424, BTC-e.com)
6134   2.737811       0                     (89891, ePay.info)
7880   2.732455       1           (Kraken.com, CoinTrader.net)
762    2.732455       1    (LocalBitcoins.com-old, Kraken.com)
7847   2.732455       1               (Kraken.com, AnxPro.com)
2593   2.700932       0                   (BtcTrade.com, 4050)
8965   2.691942       0             (ePay.info, Coin-Swap.net)
13418  2.619423       0                       (763, C-Cex.com)
5485   2.617511       0         (Bittrex.com, EvolutionMarket)
5416   2.612447       1                     (Bittrex.com, 763)
8984   2.565247       1          (ePay.info, BTC-e.com-output)
14437  2.543750       0              (OKCoin.com-2, BTC-e.com)
13927  2.516451       1       (Bitstamp.net-old, OKCoin.com-2)
4923   2.460483       0                      (OKCoin.com, 424)
8960   2.431089       0                  (ePay.info, Bter.com)
13937  2.427543       0                (Bitstamp.net-old, 424)
14934  2.422597       0          (Coin-Swap.net, Hashnest.com)
6671   2.359816       0                  (1058, Coin-Swap.net)
11959  2.357030       0             (Poloniex.com, AnxPro.com)
8851   2.357030       0         (CoinTrader.net, Poloniex.com)
692    2.357030       0  (LocalBitcoins.com-old, Poloniex.com)
9675   2.336988       0           (BTC-e.com-output, Bter.com)
4325   2.327756       0                 (NitrogenSports.eu, 0)
6781   2.271296       1                (BitcoinFog, ePay.info)
11348  2.254505       0                       (BitVC.com, 417)
4298   2.240045       0       (NitrogenSports.eu, Bittrex.com)
9616   2.238251       0                           (18479, 424)
12407  2.237566       0              (Paymium.com, AnxPro.com)
705    2.237566       0   (LocalBitcoins.com-old, Paymium.com)

In [18]:
import karateclub
from karateclub import DeepWalk,Role2Vec

In [35]:
g_CC=g1.subgraph(max(nx.connected_components(g1), key=len)).copy()

In [36]:
model= DeepWalk(dimensions=8,window_size=4)
#model= Role2Vec(dimensions=8,window_size=4)

In [37]:
new_names = {n:i for i,n in enumerate(g_CC.nodes)}
inverse = {num:name for name,num in new_names.items()}
g_CC = nx.relabel_nodes(g_CC,new_names)

In [38]:
model.fit(g_CC)

In [39]:
X = model.get_embedding()

In [40]:
new_names["OKCoin.com"]

297

In [41]:
from scipy import spatial
node = []
val=[]
for i in range(len(X)):
    v = spatial.distance.cosine(X[i], X[297])
    node.append(inverse[i])
    val.append(v)

In [42]:
display = pd.DataFrame()
display["node"]=node
display["val"]=val

In [43]:
display.sort_values("val",ascending=True)[:20]

node       val
297                          OKCoin.com  0.000000
370                             9834729  0.031355
70                                  424  0.100904
137                        BtcTrade.com  0.111413
107                                1647  0.132239
142                                4394  0.132872
181                               89891  0.149563
373                             1659009  0.153569
106                             1459726  0.200141
110                               99582  0.201890
396                              135585  0.208729
295  1NK4hddLTa5dCWACUvwTvEvMcijB5sk8zD  0.215531
47                              2974420  0.218677
388                               95391  0.222476
111                               18479  0.224258
294                                 417  0.225451
337                                1252  0.226328
271                           ChBtc.com  0.236002
11                                 1226  0.241530
167                             1471024  0.259855

In [44]:
display.sort_values("val",ascending=False)[:20]

node       val
206  17yMoeo9hxaJLMrA7XzhGHkmVAZEQ864bw  1.609273
214                        CoinArch.com  1.603134
77                               655983  1.582718
218                    SatoshiMines.com  1.516015
310  1GrwqBWKe9bhR1XY8nDtZ16guHmypWVQjB  1.513603
61                      EvolutionMarket  1.510991
335                             2696191  1.508463
101                                2268  1.506685
308                         999Dice.com  1.505978
177                            69198728  1.480292
165                            70139398  1.474395
194                              626280  1.467307
304   1DJBgoGY3wS1mnq8wJepKbFBSX4Ugtt5q  1.456232
114  15H9YckW6XXp4dNcpareoVBW3gLYZLGjjg  1.450359
198  1MAQTFwNFuVhGANupKCxeyvNPwJSiCX8qe  1.437050
45                                  175  1.436740
352                   SealsWithClubs.eu  1.432464
195  14MTQkxdZcnmNKg2q1Sb3i45jfqND6VqeB  1.432022
357                            46496912  1.422647
318                             2206529  1.421709